**<h1>Financial Data Analytics Final Team Project**

## [01] Project Definition

#### 01. 프로젝트 주제 : 개인사업자 휴폐업(기대수명) 예측모형

#### 02. 주제 선정 배경: Thin filer 개인사업자의 향후 기대수명 예측을 통해 은행권에 대출 승인 시 참고
#### 03 데이터 수집 방법 : (1) 국세청 휴폐업조회 API 및 국세청 상호조회 API (2) 나이스평가정보 사업자정보 DATA (3) 공정거래위원회 통신판매사업자 DATA 등
#### 04 데이터 전처리 방식 :  (1) 국세청 상호조회를 통해 전국 소재 사업자번호의 유효성 체크 (2) 국세청 휴폐업조회 API를 통해 휴폐업 여부 체크(데이터 탐색) (3) 나이스평가정보 사업자정보 DATA 를 통해 features 추가: 지역, 산업, 상호명 등

이 프로젝트는 **국세청 사업자 정보 및 나이스평가정보의 기업정보 데이터베이스**를 활용하여 개인사업자의 기업정보 특성을 기반으로 **개인사업자의 기대수명을 예측하는 모델**을 개발하는 것을 목표로 합니다.
1.	문제 정의
    -	목표: 개인 사업자의 예상 영업일수를 예측하는 **회귀 문제** ('영업일수(100일 단위)').
    -	비즈니스 목표: 금융을 이용할 의사와 여력이 충분함에도 은행 및 금융기관에서 거래 이력이 없다는 이유만으로 금융활동을 하는데 제한을 받는 thin filer(개인사업자)의 기대수명을 예측함으로써 보다 개선된 여신심사를 추구하고자 함.
2.	타겟 변수와 특성
    -	타겟 변수: 영업일수(100일단위)
    -	특성 변수:
        -	나라장터조달업체종업원수 : 조달청
        -	산재보험_상시근로자수 : 공공데이터포털
        -	고용보험_상시근로자수: 공공데이터포털
        -	사업자유형코드 : 나이스평가정보
        -	납세자유형코드 : 국세청
        -	산업분류코드 : 통게청 11차 표준산업분류코드 
        -	시도 : 나이스평가정보
        -   국세청상호명존재여부 :국세청
        -   개업일 : 나이스평가정보
        -	통신판매사업자여부 :공공데이터포털
        -   나라장터조달업체여부 : 조달청
        -	각 특성은 개인사업자 기대수명 예측에 영향을 미칠 수 있으며, 추가적인 파생 변수 생성으로 모델 성능 향상이 기대할 수 있음.
3.	데이터 평가
    -	데이터 출처: 국세청, 공정거래위원회, 조달청, 나이스평가정보
    -	데이터 품질:
        -	샘플 수: 약 160만개 사
        -	구성: 특성은 수치형 및 명목형 데이터로 구성.
        -	결측치 및 이상치: 일부 결측치와 이상치가 포함되어 있어 데이터 전처리가 필요.
4.	평가 지표
    -	**정확도(Accuracy)**: 모델의 분류 성능 평가를 위한 주요 지표로 사용.
5.	데이터 접근 및 프라이버시
    -	데이터 출처: 공공 데이터 개방 목적으로 공개된 데이터셋 및 신용정보사 나이스평가정보의 자체 입수 DATABASE
    -	프라이버시 고려사항: 개인 식별 정보는 포함되지 않아 데이터 프라이버시 기준을 준수.
6.	모델링 목표와 접근 방식
    -	모델링 전략:
        -	사용할 알고리즘:
            1.	Logistic Regression
            2.	K-Nearest Neighbors (KNN)
            3.	Decision Tree
            4.	Random Forest
        -	앙상블 방법:
            -	VotingClassifier를 사용하여 단일 모델의 성능을 넘어서는 예측 성능 달성.
            -	Hard Voting과 Soft Voting을 모두 시도하여 최적의 앙상블 방법 결정.
    -	분석 워크플로우:
        -	결측값 처리 및 이상치 제거를 포함한 데이터 전처리.
        -	데이터 패턴과 상관관계를 파악하기 위한 탐색적 데이터 분석(EDA).
        -	모델의 예측 성능을 향상시키기 위한 특성 공학 및 선택.
        -	모델의 일반화를 높이기 위한 교차 검증 및 하이퍼파라미터 튜닝.
        -	추후 계획: 외부 데이터셋 또는 추가적인 도메인별 특성을 활용하여 모델 적용성을 확대.
7.	리스크 및 한계
    -	리스크: 데이터셋 내 '개인'의 특성을 드러낼 수 있는 '나이', '성별' 등의 정보가 제한되어 있어 편향 가능성 존재.
    -	한계: 결측값 처리 방식이 모델 성능에 영향을 미칠 수 있음.


In [13]:
import pandas as pd
import numpy as np
import zipfile
from datetime import datetime

from sklearn.pipeline import Pipeline
from sklearn.ensemble import IsolationForest
from sklearn.neighbors import LocalOutlierFactor
from sklearn.experimental import enable_iterative_imputer  # IterativeImputer 사용을 명시적으로 활성화
from sklearn.impute import SimpleImputer, KNNImputer, IterativeImputer
from sklearn.preprocessing import OneHotEncoder, OrdinalEncoder, StandardScaler, PolynomialFeatures
from sklearn.compose import ColumnTransformer
from sklearn.neighbors import KNeighborsRegressor
from sklearn.linear_model import LinearRegression, Ridge, ElasticNet, Lasso
from sklearn.model_selection import train_test_split, RandomizedSearchCV, GridSearchCV
from sklearn.metrics import mean_squared_error
from sklearn.base import BaseEstimator, TransformerMixin


## [02] Data Description
### 등록국세청코드
- 101 ~ 999의 값으로 신규개업자에게 사용 가능한 번호 101-999를 순차적으로 부여합니다.<br>
- 사업자등록번호를 최초부여한 관할 세무서의 코드

### 납세자유형코드
- 개인구분 코드<br>
     ① 개인과세사업자는 특정 동 구별없이 01부터 79까지를 순차적으로 부여<br>
     ② 개인면세사업자는 산업 구분없이 90부터 99까지를 순차적으로 부여<br>
     ③ 소득세법 제2조 제3항에 해당하는 법인이 아닌 종교 단체 : 89<br>
     ④ 소득세법 제2조 제3항에 해당하는 자로서 "(3)"이외의자(아파트관리사무소 등) 및 다단계판매원 : 80<br>
<br><br>
- 법인성격코드：법인에 대하여는 성격별 코드를 구분하여 사용한다.<br>
     ① 영리법인의 본점 81，86，87, 88<br>
     ② 비영리법인의 본점 및 지점(법인격 없는 사단，재단，기타 단체 중 법인으로 보는 단체를 포함) : 82<br>
     ③ 국가，지방자치단체，지방자치단체조합 : 83<br>
     ④ 외국법인의 본・지점 및 연락사무소 : 84<br>
     ⑤ 영리법인의 지점 : 85<br>

## [03] Data Acquisition and Preprocessing

In [2]:
# 데이터 읽기, 용량 절약을 위해 zip 파일의 압축을 해제하지 않고 바로 읽도록 한다.
with zipfile.ZipFile('20241112.zip') as zf:
    with zf.open('20241112.csv') as file:
        df_source = pd.read_csv(file, dtype={
            '사업자등록번호': 'string', 
            '등록국세청코드': 'string', 
            '납세자유형코드': 'string',
            '사업자유형코드': 'string', 
            '산업분류코드': 'string', 
            '시도': 'string',
            '국세청상호명': 'string', 
            '국세청상호명존재여부': 'string', 
            '영업일수': 'int',
            '영업일수(100일단위)': 'int', 
            '개업일': 'string', 
            '폐업일': 'string', 
            '통신판매사업자여부': 'string',
            '통신판매사업자전화번호': 'string', 
            '통신판매사업자전자우편': 'string',
            '나라장터조달업체제조구분코드': 'string', 
            '고용보험 업종코드': 'string', 
            '나라장터조달업체업무구분코드': 'string',
            '사업장 우편번호': 'string'
        })
df_source.columns = df_source.columns.str.strip().str.replace(' ', '_')
display(df_source)


사업자등록번호 등록국세청코드 사업자유형코드 납세자유형코드 산업분류코드  시도              국세청상호명  \
0        1010109091     101      01      01  56114  서울             김밥천국삼청점   
1        1010109107     101      01      01  56122  서울               명송 하나   
2        1010112688     101      01      01  47312  서울                가인전자   
3        1010112733     101      01      01  20400  서울               켐스펙교역   
4        1010112806     101      01      01  46596  서울               동광전업사   
...             ...     ...     ...     ...    ...  ..                 ...   
1595328  8999100276     899      91      04  03112  경북            제2007대성호   
1595329  8999300310     899      93      04  46312  부산                경북농산   
1595330  8999601213     899      96      04  90212  대구              글나루독서실   
1595331  8999700981     899      97      04  96921  전북                  길묘   
1595332  9048400148     904      84      04  75999  서울  마쓰시마 메저 테크 서울연락사무소   

        국세청상호명존재여부  영업일수  영업일수(100일단위)  ... 사업장_우편번호 사업장_주소 고용보험_업종코드  \
0                Y  4766            48  ...     <NA>    NaN      <NA>   
1                Y  5791            58  ...     <NA>    NaN      <NA>   
2                Y  2586            26  ...     <NA>    NaN      <NA>   
3                Y  2371            24  ...     <NA>    NaN      <NA>   
4                Y  2477            25  ...     <NA>    NaN      <NA>   
...            ...   ...           ...  ...      ...    ...       ...   
1595328          Y  2146            21  ...     <NA>    NaN      <NA>   
1595329          Y  2023            20  ...     <NA>    NaN      <NA>   
1595330          Y   868             9  ...     <NA>    NaN      <NA>   
1595331          Y   363             4  ...     <NA>    NaN      <NA>   
1595332          Y  4140            41  ...     <NA>    NaN      <NA>   

        고용보험_업종명 산재보험_성립일자 고용보험_성립일자 산재보험_상시근로자수 고용보험_상시근로자수 산재보험_사업구분  \
0            NaN       NaN       NaN         NaN         NaN       NaN   
1            NaN       NaN       NaN         NaN         NaN       NaN   
2            NaN       NaN       NaN         NaN         NaN       NaN   
3            NaN       NaN       NaN         NaN         NaN       NaN   
4            NaN       NaN       NaN         NaN         NaN       NaN   
...          ...       ...       ...         ...         ...       ...   
1595328      NaN       NaN       NaN         NaN         NaN       NaN   
1595329      NaN       NaN       NaN         NaN         NaN       NaN   
1595330      NaN       NaN       NaN         NaN         NaN       NaN   
1595331      NaN       NaN       NaN         NaN         NaN       NaN   
1595332      NaN       NaN       NaN         NaN         NaN       NaN   

        고용보험_사업구분  
0             NaN  
1             NaN  
2             NaN  
3             NaN  
4             NaN  
...           ...  
1595328       NaN  
1595329       NaN  
1595330       NaN  
1595331       NaN  
1595332       NaN  

[1595333 rows x 44 columns]

In [3]:
# 개인사업자의 데이터만 남긴다. (81 ~ 88 제외)
df_stage1 = df_source[(df_source['사업자유형코드'] <= '80') | (df_source['사업자유형코드'] >= '89')]
display(df_stage1)

사업자등록번호 등록국세청코드 사업자유형코드 납세자유형코드 산업분류코드  시도              국세청상호명  \
0        1010109091     101      01      01  56114  서울             김밥천국삼청점   
1        1010109107     101      01      01  56122  서울               명송 하나   
2        1010112688     101      01      01  47312  서울                가인전자   
3        1010112733     101      01      01  20400  서울               켐스펙교역   
4        1010112806     101      01      01  46596  서울               동광전업사   
...             ...     ...     ...     ...    ...  ..                 ...   
1595327  8999001055     899      90      04  85709  경기  아트앤하트 고양탄현에듀포레푸르지오   
1595328  8999100276     899      91      04  03112  경북            제2007대성호   
1595329  8999300310     899      93      04  46312  부산                경북농산   
1595330  8999601213     899      96      04  90212  대구              글나루독서실   
1595331  8999700981     899      97      04  96921  전북                  길묘   

        국세청상호명존재여부  영업일수  영업일수(100일단위)  ... 사업장_우편번호 사업장_주소 고용보험_업종코드  \
0                Y  4766            48  ...     <NA>    NaN      <NA>   
1                Y  5791            58  ...     <NA>    NaN      <NA>   
2                Y  2586            26  ...     <NA>    NaN      <NA>   
3                Y  2371            24  ...     <NA>    NaN      <NA>   
4                Y  2477            25  ...     <NA>    NaN      <NA>   
...            ...   ...           ...  ...      ...    ...       ...   
1595327          Y   690             7  ...     <NA>    NaN      <NA>   
1595328          Y  2146            21  ...     <NA>    NaN      <NA>   
1595329          Y  2023            20  ...     <NA>    NaN      <NA>   
1595330          Y   868             9  ...     <NA>    NaN      <NA>   
1595331          Y   363             4  ...     <NA>    NaN      <NA>   

        고용보험_업종명 산재보험_성립일자 고용보험_성립일자 산재보험_상시근로자수 고용보험_상시근로자수 산재보험_사업구분  \
0            NaN       NaN       NaN         NaN         NaN       NaN   
1            NaN       NaN       NaN         NaN         NaN       NaN   
2            NaN       NaN       NaN         NaN         NaN       NaN   
3            NaN       NaN       NaN         NaN         NaN       NaN   
4            NaN       NaN       NaN         NaN         NaN       NaN   
...          ...       ...       ...         ...         ...       ...   
1595327      NaN       NaN       NaN         NaN         NaN       NaN   
1595328      NaN       NaN       NaN         NaN         NaN       NaN   
1595329      NaN       NaN       NaN         NaN         NaN       NaN   
1595330      NaN       NaN       NaN         NaN         NaN       NaN   
1595331      NaN       NaN       NaN         NaN         NaN       NaN   

        고용보험_사업구분  
0             NaN  
1             NaN  
2             NaN  
3             NaN  
4             NaN  
...           ...  
1595327       NaN  
1595328       NaN  
1595329       NaN  
1595330       NaN  
1595331       NaN  

[1114301 rows x 44 columns]

In [4]:
# 필요한 컬럼들로 DataFrame 재구성
df_stage2 = df_stage1[['사업자유형코드','납세자유형코드','산업분류코드','시도','국세청상호명존재여부','영업일수(100일단위)','개업일','통신판매사업자여부',
                       '나라장터조달업체여부','나라장터조달업체종업원수','산재보험_상시근로자수','고용보험_상시근로자수']].assign(개업일=lambda x: x['개업일'].str[:4])

# Float --> Int로 변환
df_stage2['나라장터조달업체종업원수'] = pd.to_numeric(df_stage2['나라장터조달업체종업원수'],errors='coerce', downcast=None).astype('Int64')
df_stage2['산재보험_상시근로자수'] = pd.to_numeric(df_stage2['산재보험_상시근로자수'],errors='coerce', downcast=None).astype('Int64')
df_stage2['고용보험_상시근로자수'] = pd.to_numeric(df_stage2['고용보험_상시근로자수'],errors='coerce', downcast=None).astype('Int64')

# Drop duplicates
df_stage2 = df_stage2.drop_duplicates()

display(df_stage2)

사업자유형코드 납세자유형코드 산업분류코드  시도 국세청상호명존재여부  영업일수(100일단위)   개업일 통신판매사업자여부  \
0            01      01  56114  서울          Y            48  1994         N   
1            01      01  56122  서울          Y            58  1994         N   
2            01      01  47312  서울          Y            26  1997         N   
3            01      01  20400  서울          Y            24  1997         N   
4            01      01  46596  서울          Y            25  1997         N   
...         ...     ...    ...  ..        ...           ...   ...       ...   
1595327      90      04  85709  경기          Y             7  2020         N   
1595328      91      04  03112  경북          Y            21  2016         N   
1595329      93      04  46312  부산          Y            20  2016         N   
1595330      96      04  90212  대구          Y             9  2020         N   
1595331      97      04  96921  전북          Y             4  2020         N   

        나라장터조달업체여부  나라장터조달업체종업원수  산재보험_상시근로자수  고용보험_상시근로자수  
0                N          <NA>         <NA>         <NA>  
1                N          <NA>         <NA>         <NA>  
2                N          <NA>         <NA>         <NA>  
3                N          <NA>         <NA>         <NA>  
4                N          <NA>         <NA>         <NA>  
...            ...           ...          ...          ...  
1595327          N          <NA>         <NA>         <NA>  
1595328          N          <NA>         <NA>         <NA>  
1595329          N          <NA>         <NA>         <NA>  
1595330          N          <NA>         <NA>         <NA>  
1595331          N          <NA>         <NA>         <NA>  

[1051967 rows x 12 columns]

# [04] Data Exploration

In [18]:
# 데이터 탐색용 데이터프레임 정의
df_exploration = df_stage2.copy()
df_exploration.head()

사업자유형코드 납세자유형코드 산업분류코드  시도 국세청상호명존재여부  영업일수(100일단위)   개업일 통신판매사업자여부  \
0      01      01  56114  서울          Y            48  1994         N   
1      01      01  56122  서울          Y            58  1994         N   
2      01      01  47312  서울          Y            26  1997         N   
3      01      01  20400  서울          Y            24  1997         N   
4      01      01  46596  서울          Y            25  1997         N   

  나라장터조달업체여부  나라장터조달업체종업원수  산재보험_상시근로자수  고용보험_상시근로자수  
0          N          <NA>         <NA>         <NA>  
1          N          <NA>         <NA>         <NA>  
2          N          <NA>         <NA>         <NA>  
3          N          <NA>         <NA>         <NA>  
4          N          <NA>         <NA>         <NA>

In [19]:
df_exploration.info()

<class 'pandas.core.frame.DataFrame'>
Index: 1051967 entries, 0 to 1595331
Data columns (total 12 columns):
 #   Column        Non-Null Count    Dtype 
---  ------        --------------    ----- 
 0   사업자유형코드       1051967 non-null  string
 1   납세자유형코드       1051967 non-null  string
 2   산업분류코드        1051967 non-null  string
 3   시도            1051967 non-null  string
 4   국세청상호명존재여부    1051967 non-null  string
 5   영업일수(100일단위)  1051967 non-null  int64 
 6   개업일           1051967 non-null  string
 7   통신판매사업자여부     1051967 non-null  string
 8   나라장터조달업체여부    1051967 non-null  object
 9   나라장터조달업체종업원수  47590 non-null    Int64 
 10  산재보험_상시근로자수   21051 non-null    Int64 
 11  고용보험_상시근로자수   21051 non-null    Int64 
dtypes: Int64(3), int64(1), object(1), string(7)
memory usage: 139.6+ MB


In [20]:
df_exploration.describe()

영업일수(100일단위)  나라장터조달업체종업원수  산재보험_상시근로자수  고용보험_상시근로자수
count  1.051967e+06       47590.0      21051.0      21051.0
mean   3.025837e+01      4.696764     3.158757     2.915728
std    3.465013e+01       10.2767     8.116572     7.422526
min   -6.569000e+03           0.0          0.0          0.0
25%    1.100000e+01           1.0          1.0          1.0
50%    2.300000e+01           3.0          1.0          1.0
75%    4.200000e+01           5.0          3.0          3.0
max    7.377000e+03        1014.0        410.0        412.0

In [21]:
df_exploration.nunique()

사업자유형코드           91
납세자유형코드            6
산업분류코드          1604
시도                34
국세청상호명존재여부         2
영업일수(100일단위)     406
개업일              136
통신판매사업자여부          2
나라장터조달업체여부         2
나라장터조달업체종업원수     118
산재보험_상시근로자수      104
고용보험_상시근로자수       99
dtype: int64

In [22]:
# 피처 타입 정의
target           = ['영업일수(100일단위)']
numeric_features = ['나라장터조달업체종업원수', '산재보험_상시근로자수', '고용보험_상시근로자수']
ordinal_features = []
nominal_features = ['사업자유형코드','납세자유형코드','산업분류코드','시도','국세청상호명존재여부','개업일','통신판매사업자여부','나라장터조달업체여부']
drop_na_features = []

In [ ]:
## Numeric Variable
import matplotlib.pyplot as plt
import platform
from pandas.plotting import scatter_matrix
from matplotlib import rc


# 1. 운영 체제에 따라 한글 폰트 설정
if platform.system() == "Windows":
    rc('font', family='Malgun Gothic')  # Windows: 맑은 고딕
elif platform.system() == "Darwin":
    rc('font', family='AppleGothic')   # macOS: 애플 고딕
else:
    rc('font', family='NanumGothic')   # Linux: 나눔 고딕

df_numeric = df_exploration[numeric_features + numeric_features]
df_numeric.hist(bins=50, figsize=(20,15)) 
plt.show()

# 모든 변수에 대해 scatter matrix 그리기
scatter_matrix(df_numeric, figsize=(15, 15), diagonal='hist', alpha=0.5)
plt.suptitle('Scatter Matrix of Numeric Variables', fontsize=12)
plt.show()

# 상관 행렬
import seaborn as sns
plt.figure(figsize=(10, 8))
corr_before = df_numeric.corr()
sns.heatmap(corr_before, annot=True, cmap='coolwarm', vmin=-1, vmax=1)
plt.title(f'Correlation Matrix (Before Log Transformation)')
plt.show()

In [ ]:
import matplotlib.pyplot as plt

# df_numeric 각 변수들에 대한 박스플롯을 그리기
plt.figure(figsize=(15, 10))
df_numeric.boxplot(column=df_numeric.columns.tolist())
plt.title('Boxplots of Numeric Variables')
plt.xticks(rotation=45)  # x축 레이블 가독성을 위해 회전
plt.show()

**수치형 데이터 탐색 결과**

1. **로그 변환 고려**
    - 오른쪽 꼬리가 긴 분포를 보이는 대부분의 변수들
    - 분포를 정규분포에 가깝게 하기 위해 **로그 변환** 적용
    - 로그 변환 후, 분석 및 모델링의 성능 개선 기대

2. **상관관계 높은 변수의 처리**
    - 변수 간 높은 상관관계로 **다중공선성** 발생 가능성
    - 다중공선성 문제를 해결하기 위해 차원 축소 기법(**PCA**) 적용 또는 불필요한 변수 제거 고려

3. **모델링을 위한 데이터 전처리**
    - 로그 변환 및 이상치 제거 후 다시 분포 및 상관관계 분석
    - **다중공선성 해결**을 위해 필요시 변수를 제거하거나 대체하여 최적의 변수 선정


In [ ]:
import numpy as np

# 로그 변환 (0 이상의 값에 대해서만 적용)
df_log_numeric = df_numeric.copy()
df_log_numeric = df_log_numeric[['나라장터조달업체종업원수', '산재보험_상시근로자수', '고용보험_상시근로자수']]
df_log_numeric = np.log1p(df_log_numeric)

# 로그 변환 후 히스토그램
df_log_numeric.hist(bins=50, figsize=(20, 15))
plt.suptitle('Histograms of Log Transformed Numeric Variables', fontsize=16)
plt.show()

# 로그 변환 후 산점도 행렬
scatter_matrix(df_log_numeric, figsize=(15, 15), diagonal='hist', alpha=0.5)
plt.suptitle('Scatter Matrix of Log Transformed Numeric Variables', fontsize=16)
plt.show()

# 로그 변환 후 상관 행렬
plt.figure(figsize=(10, 8))
corr_after = df_log_numeric.corr()
sns.heatmap(corr_after, annot=True, cmap='RdBu', vmin=-1, vmax=1)
plt.title('Correlation Matrix (After Log Transformation)')
plt.show()

In [ ]:
import matplotlib.pyplot as plt

# df_log_numeric 각 변수들에 대한 박스플롯을 그리기
plt.figure(figsize=(15, 10))
df_log_numeric.boxplot(column=df_log_numeric.columns.tolist())
plt.title('Boxplots of Numeric Variables')
plt.xticks(rotation=45)  # x축 레이블 가독성을 위해 회전
plt.show()

# [05] Data Preparation and Model Setup

In [39]:
df_source = df_stage2.copy()

# 피처 타입 정의
target           = ['영업일수(100일단위)']
numeric_features = ['나라장터조달업체종업원수', '산재보험_상시근로자수', '고용보험_상시근로자수']
ordinal_features = []
nominal_features = ['사업자유형코드','납세자유형코드','산업분류코드','시도','국세청상호명존재여부','개업일','통신판매사업자여부','나라장터조달업체여부']
drop_na_features = []

# 특성과 타겟 변수 분리
y = df_source[target]
X = df_source[numeric_features + ordinal_features + nominal_features]

# 이상치 제거 함수 (도메인 지식 활용 ) 정의
def remove_domain_outliers(X, y=None):
        X_cleaned = X.copy()     
        X_cleaned = \
        X_cleaned[(df_source.나라장터조달업체종업원수 <= 1000) &
                (df_source.산재보험_상시근로자수 <= 1000) & 
                (df_source.고용보험_상시근로자수 <= 1000)]
        if y is not None:
            y_cleaned = y.loc[X_cleaned.index]  # 타겟 데이터프레임의 인덱스 동기화
            return X_cleaned, y_cleaned
        return X_cleaned

# 이상치 제거기 (자동 ) 설정
# auto_outlier_remover = None  # 이상치 제거기 설정하지 않음
# auto_outlier_remover = LocalOutlierFactor(n_neighbors=5, contamination=0.1) 
auto_outlier_remover = IsolationForest(random_state=42, contamination=0.05)
auto_outlier_removers = [
     None,
     LocalOutlierFactor(n_neighbors=10, contamination=0.1),
     IsolationForest(random_state=42, contamination=0.05)
]

# 사용자 정의 Transformer
class FeatureCombiner(BaseEstimator, TransformerMixin):
        def __init__(self, combined_features=[]):
            self.combined_features = combined_features
            pass

        def fit(self, X, y=None):
            return self  # 이 Transformer는 학습이 필요하지 않음
        
        def transform(self, X):
            X = pd.DataFrame(X, columns=numeric_features)
            self.X_combined = pd.DataFrame()
            # 새로운 특성 생성
            if 'AVG_WORKFORCE' in self.combined_features:
                self.X_combined['AVG_WORKFORCE'] = (X['나라장터조달업체종업원수'] + X['산재보험_상시근로자수'] + X['고용보험_상시근로자수']) / 3
            if 'TOTAL_WORKFORCE' in self.combined_features:
                self.X_combined['TOTAL_WORKFORCE'] = (X['나라장터조달업체종업원수'] + X['산재보험_상시근로자수'] + X['고용보험_상시근로자수'])
            return pd.concat([self.X_combined], axis=1)
        
        def get_feature_names_out(self, input_features=None):
             # 새로 생성된 특성과 기존 numeric features 이름을 합쳐 반환
             return self.X_combined.columns.tolist()
        
algorithms = [
     LinearRegression(),
     Ridge(random_state=42, max_iter=10000000),
     Lasso(random_state=42, max_iter=10000000),
     ElasticNet(random_state=42, max_iter=10000000),
     KNeighborsRegressor(),
]

params_common = {
     'preprocessor__numeric_transformer__numeric_imputer__strategy' : ['median', 'mean', 'most_frequent'],
     'preprocessor__numeric_transformer__feature_combiner__combined_features' : [
          ['TOTAL_WORKFORCE', 'AVG_WORKFORCE'],
          ['TOTAL_WORKFORCE'],
          []
     ],
     'preprocessor__numeric_transformer__polynomial_features__degree' : [1, 2, 3],
}

params_model = {}
params_model['LinearRegression'] = {}
params_model['Ridge'] = {'algorithm__alpha': [0.01, 0.1, 1.0, 10.0, 100.0],}  # 다양한 alpha 값
params_model['Lasso'] = {'algorithm__alpha': [0.01, 0.1, 1.0, 10.0, 100.0],}  # 다양한 alpha 값
params_model['ElasticNet'] = {
    'algorithm__alpha': [0.01, 0.1, 1.0, 10.0, 100.0],
    'algorithm__l1_ratio': [0.1, 0.3, 0.5, 0.7, 0.9],
}
params_model['KNeighborsRegressor'] = {
    'algorithm__n_neighbors': range(3, 51),         # k-NN의 k 값 (이웃 개수)
    'algorithm__weights': ['uniform', 'distance'],  # 가중치 옵션
    'algorithm__p': [1, 2],                         # 거리 측정 방식 (1: 맨해튼 거리, 2: 유클리드 거리)
}

searches = {}

for algorithm in algorithms:
    algorithm_name = algorithm.__class__.__name__
    print(f"Processing {algorithm_name}...")
    # 수치형 데이터 전처리 파이프라인
    numeric_transformer = Pipeline(
        steps=[
            ('numeric_imputer'      , SimpleImputer()),
            ('feature_combiner'     , FeatureCombiner()),
            ('polynomial_features'  , PolynomialFeatures(include_bias=False)),
            ('numeric_scaler'       , StandardScaler()),
        ]
    )
    # 서열형 데이터 전처리 파이프라인
    ordinal_transformer = Pipeline(
        steps=[
            ('ordinal_imputer'      , SimpleImputer(strategy='constant', fill_value="None")),
            ('ordinal_encoder'      , OrdinalEncoder(categories=[['None', 'Old', 'Recent']])),
        ]
    )
    # 명목형 데이터 전처리 파이프라인
    nominal_transformer = Pipeline(
        steps=[
            ('nominal_imputer'      , SimpleImputer(strategy='most_frequent')),
            ('nominal_encoder'      , OneHotEncoder(drop='first', handle_unknown='infrequent_if_exist')),
        ]
    )
    # 전체 전처리기 - 각 타입별로 변수 처리 및 결합
    preprocessor = ColumnTransformer(
        transformers=[
            ('numeric_transformer'  , numeric_transformer, numeric_features),
            ('ordinal_transformer'  , ordinal_transformer, ordinal_features),
            ('nominal_transformer'  , nominal_transformer, nominal_features),
        ]
    )
    # 전체 파이프라인
    model = Pipeline(
        steps=[
            ('preprocessor'         , preprocessor),
            ('algorithm'            , algorithm),
        ]
    )
    # [10] RandomizedSearchCV를 위한 파라미터 정의
    params = params_common.copy()
    params.update(params_model[algorithm_name])
    display(f"{algorithm_name}'s params:", params)

    # [10] RandomizedSearchCV 초기화
    search = RandomizedSearchCV(
        estimator=model, 
        param_distributions=params, # param_grid(GridSearchCV) 대신 param_distributions 사용
        cv=5, 
        scoring='r2',
        n_jobs=-1,
        n_iter=1000,                 # 파라미터 조합 중 100개 샘플링. GridSearchCV는 모든 파라미터 사용
        random_state=42,            # 재현성을 위해 random_state 설정
    )
    search_key = (
        algorithm.__class__.__name__,
        SimpleImputer().__class__.__name__
    )
    searches[search_key] = search  # [10] search를 딕셔너리에 저장

# [10] 모형(파이프라인)의 구조를 시각적으로 표현
for key, search in searches.items():
    display(f"Search: {key}", search)

# 훈련 세트와 테스트 세트 분할
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# 중복 데이터 제거
mask_dups = X_train.duplicated(keep=False)
display("Duplicated Samples:", X_train[mask_dups])
X_train = X_train.drop_duplicates()
y_train = y_train.loc[X_train.index]
display(X_train)
display(y_train)

Processing LinearRegression...


"LinearRegression's params:"

{'preprocessor__numeric_transformer__numeric_imputer__strategy': ['median',
  'mean',
  'most_frequent'],
 'preprocessor__numeric_transformer__feature_combiner__combined_features': [['TOTAL_WORKFORCE',
   'AVG_WORKFORCE'],
  ['TOTAL_WORKFORCE'],
  []],
 'preprocessor__numeric_transformer__polynomial_features__degree': [1, 2, 3]}

Processing Ridge...


"Ridge's params:"

...

RandomizedSearchCV(cv=5,
                   estimator=Pipeline(steps=[('preprocessor',
                                              ColumnTransformer(transformers=[('numeric_transformer',
                                                                               Pipeline(steps=[('numeric_imputer',
                                                                                                SimpleImputer()),
                                                                                               ('feature_combiner',
                                                                                                FeatureCombiner()),
                                                                                               ('polynomial_features',
                                                                                                PolynomialFeatures(include_bias=False)),
                                                                                               ('numeric_scaler',
                                                                                                StandardScaler())]),
                                                                               ['나라장터조달업체종업원수',
                                                                                '산재보험_상시근로자수',
                                                                                '고용보험_상...
                                        'algorithm__weights': ['uniform',
                                                               'distance'],
                                        'preprocessor__numeric_transformer__feature_combiner__combined_features': [['TOTAL_WORKFORCE',
                                                                                                                    'AVG_WORKFORCE'],
                                                                                                                   ['TOTAL_WORKFORCE'],
                                                                                                                   []],
                                        'preprocessor__numeric_transformer__numeric_imputer__strategy': ['median',
                                                                                                         'mean',
                                                                                                         'most_frequent'],
                                        'preprocessor__numeric_transformer__polynomial_features__degree': [1,
                                                                                                           2,
                                                                                                           3]},
                   random_state=42, scoring='r2')

'Duplicated Samples:'

나라장터조달업체종업원수  산재보험_상시근로자수  고용보험_상시근로자수 사업자유형코드 납세자유형코드 산업분류코드   시도  \
834544           <NA>         <NA>         <NA>      06      01  47320   서울   
988423           <NA>         <NA>         <NA>      29      01  68112  충남    
140840           <NA>         <NA>         <NA>      91      04  47210   서울   
489428           <NA>         <NA>         <NA>      01      01  47414   경기   
1500493          <NA>         <NA>         <NA>      32      01  56213   부산   
...               ...          ...          ...     ...     ...    ...  ...   
246892           <NA>         <NA>         <NA>      04      02  56199   인천   
411256           <NA>         <NA>         <NA>      27      01  46596   경기   
228428           <NA>         <NA>         <NA>      07      01  46699   서울   
1053857          <NA>         <NA>         <NA>      04      01  56213   전북   
210068           <NA>         <NA>         <NA>      12      01  46599   서울   

        국세청상호명존재여부   개업일 통신판매사업자여부 나라장터조달업체여부  
834544           Y  2008         N          N  
988423           Y  2011         N          N  
140840           Y  2008         N          N  
489428           Y  2000         N          N  
1500493          Y  2011         N          N  
...            ...   ...       ...        ...  
246892           Y  2000         N          N  
411256           Y  2005         N          N  
228428           Y  2004         N          N  
1053857          Y  1999         N          N  
210068           Y  1990         N          N  

[349058 rows x 11 columns]

나라장터조달업체종업원수  산재보험_상시근로자수  고용보험_상시근로자수 사업자유형코드 납세자유형코드 산업분류코드  시도  \
308872           <NA>         <NA>         <NA>      32      01  96112  경기   
1402905          <NA>         <NA>         <NA>      06      01  27196  경남   
834544           <NA>         <NA>         <NA>      06      01  47320  서울   
251479           <NA>         <NA>         <NA>      14      01  62010  인천   
369319           <NA>         <NA>         <NA>      40      01  76310  충북   
...               ...          ...          ...     ...     ...    ...  ..   
1225324          <NA>         <NA>         <NA>      02      01  47223  대구   
503329           <NA>         <NA>         <NA>      14      01  47413  경기   
1391481          <NA>            4            4      11      01  46109  부산   
1142283          <NA>         <NA>         <NA>      08      01  47813  전남   
193103           <NA>         <NA>         <NA>      11      01  47812  서울   

        국세청상호명존재여부   개업일 통신판매사업자여부 나라장터조달업체여부  
308872           N  2003         N          N  
1402905          Y  1985         N          N  
834544           Y  2008         N          N  
251479           Y  2005         N          N  
369319           Y  2009         N          N  
...            ...   ...       ...        ...  
1225324          Y  1983         N          N  
503329           Y  1993         N          N  
1391481          Y  2010         N          N  
1142283          Y  1989         N          N  
193103           Y  2008         Y          N  

[596867 rows x 11 columns]

영업일수(100일단위)
308872             49
1402905            33
834544             12
251479              1
369319             17
...               ...
1225324           142
503329             30
1391481            48
1142283             8
193103              5

[596867 rows x 1 columns]

## [06] Model Training

In [40]:
import warnings
# 모든 경고 무시: 경고를 무시하면 중요한 문제를 놓칠 수 있으므로, 가능하면 경고의 원인을 분석하여 문제를 해결하는 것이 바람직
warnings.filterwarnings("ignore")

In [41]:
################################################################################
# 모형 훈련
################################################################################

# 1.  결측치 처리
# 1.1 특정 열에 결측치 포함 시 제거
X_train = X_train.dropna(subset=[drop_na_features])
y_train = y_train.loc[X_train.index]

# 2.  이상치 제거
# 2.1 이상치 제거 - 도메인 지식 활용 및 자동 제거기 적용
X_train, y_train = remove_domain_outliers(X_train, y_train)

# [10] 여러 모형을 저장하기 위해 dictionary 사용
models = {}                         # 모형을 저장할 딕셔너리
performances = {}                   # 각 모델의 성능을 저장할 딕셔너리
best_train_score = float('-inf')    # 가장 높은 R² 값을 기록하기 위한 변수
best_model = None                   # 최적 모델을 저장하기 위한 변수
best_key = None                     # 최적 모델의 키를 저장하기 위한 변수

for auto_outlier_remover in auto_outlier_removers:
    outlier_remover_name = auto_outlier_remover.__class__.__name__
    print(f"\nApplying Auto Outlier Remover: {outlier_remover_name}")

    # 2.2 자동 이상치 제거기 적용
    if auto_outlier_remover is not None:
        # y_train_inlier = auto_outlier_remover.fit_predict(X_train[numeric_features])
        imputer = SimpleImputer(strategy='median')
        X_train_imputed = imputer.fit_transform(X_train[numeric_features])
        y_train_inlier = auto_outlier_remover.fit_predict(X_train_imputed)
        inlier_mask_train = y_train_inlier != -1
    else:
        # auto_outlier_remover가 None인 경우, 모든 데이터가 inlier로 간주
        inlier_mask_train = np.ones(X_train.shape[0], dtype=bool)  # 모든 값이 True

    # inlier 마스크에 따라 데이터 필터링
    X_train, y_train = X_train[inlier_mask_train], y_train[inlier_mask_train]

    for key, search in searches.items():    # [10] 반복문을 통해 여러 search를 fitting
        print(f"Training {key}...")

        # 5. 모형 훈련
        # 5.1  모형 적합 (모형에는 아래의 기능이 파이프라인에 포함됨)
        search.fit(X_train, y_train.values.ravel())    # model 대신 search를 적합(fitting)
        model = search.best_estimator_
        model.fit(X_train, y_train.values.ravel())
        
        full_key = (outlier_remover_name, *key) # models 딕셔너리의 키에 outlier_remover_name 추가
        models[full_key] = model  # 모델을 models 딕셔너리에 저장

        # 교차검증 성능 출력
        train_score = search.best_score_
        print(f"Best Score (R²): {train_score:.4f}")
        performances[full_key] = train_score

        # 5.4 최적 모델의 하이퍼파라미터 출력
        df_search_results = pd.DataFrame(search.cv_results_)
        display("Best Hyperparameters:", search.best_params_)  # 튜닝된 하이퍼파라미터 출력
        # display("Search Results:", pd.DataFrame(search.cv_results_))    # 교차검증결과 출력

        # 가장 높은 R² 값을 가진 모델을 best_model로 설정
        if train_score > best_train_score:
            best_train_score = train_score
            best_model = model
            best_key = full_key

# 최적 모델과 그 성능 정보 출력
print(f"Best Model R²: {best_train_score:.4f}")
print(f"Best Model: {best_key}")
display(best_model)

# 모든 모델의 성능 출력
print("All Model Performances:")
for key, score in performances.items():
    print(f"{key}: R² = {score:.4f}")


Applying Auto Outlier Remover: NoneType
Training ('LinearRegression', 'SimpleImputer')...


/Users/jinyong/anaconda3/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:227: UserWarning: Found unknown categories in columns [2] during transform. These unknown categories will be encoded as all zeros
  warnings.warn(
/Users/jinyong/anaconda3/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:227: UserWarning: Found unknown categories in columns [0, 2, 3, 5] during transform. These unknown categories will be encoded as all zeros
  warnings.warn(
/Users/jinyong/anaconda3/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:227: UserWarning: Found unknown categories in columns [0, 2] during transform. These unknown categories will be encoded as all zeros
  warnings.warn(
/Users/jinyong/anaconda3/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:227: UserWarning: Found unknown categories in columns [0, 2] during transform. These unknown categories will be encoded as all zeros
  warnings.warn(
/Users/jinyong/anaconda3/lib/python3.11/s

Best Score (R²): 0.9801


'Best Hyperparameters:'

{'preprocessor__numeric_transformer__polynomial_features__degree': 1,
 'preprocessor__numeric_transformer__numeric_imputer__strategy': 'median',
 'preprocessor__numeric_transformer__feature_combiner__combined_features': ['TOTAL_WORKFORCE',
  'AVG_WORKFORCE']}

...

'Best Hyperparameters:'

{'preprocessor__numeric_transformer__polynomial_features__degree': 1,
 'preprocessor__numeric_transformer__numeric_imputer__strategy': 'most_frequent',
 'preprocessor__numeric_transformer__feature_combiner__combined_features': ['TOTAL_WORKFORCE'],
 'algorithm__weights': 'distance',
 'algorithm__p': 1,
 'algorithm__n_neighbors': 8}

Best Model R²: 0.9881
Best Model: ('NoneType', 'Ridge', 'SimpleImputer')


Pipeline(steps=[('preprocessor',
                 ColumnTransformer(transformers=[('numeric_transformer',
                                                  Pipeline(steps=[('numeric_imputer',
                                                                   SimpleImputer(strategy='median')),
                                                                  ('feature_combiner',
                                                                   FeatureCombiner(combined_features=['TOTAL_WORKFORCE'])),
                                                                  ('polynomial_features',
                                                                   PolynomialFeatures(degree=1,
                                                                                      include_bias=False)),
                                                                  ('numeric_scaler',
                                                                   StandardScaler())]),
                                                  ['나라장터조달...
                                                                                               'Recent']]))]),
                                                  []),
                                                 ('nominal_transformer',
                                                  Pipeline(steps=[('nominal_imputer',
                                                                   SimpleImputer(strategy='most_frequent')),
                                                                  ('nominal_encoder',
                                                                   OneHotEncoder(drop='first',
                                                                                 handle_unknown='infrequent_if_exist'))]),
                                                  ['사업자유형코드', '납세자유형코드',
                                                   '산업분류코드', '시도', '국세청상호명존재여부',
                                                   '개업일', '통신판매사업자여부',
                                                   '나라장터조달업체여부'])])),
                ('algorithm',
                 Ridge(alpha=0.01, max_iter=10000000, random_state=42))])

All Model Performances:
('NoneType', 'LinearRegression', 'SimpleImputer'): R² = 0.9801
('NoneType', 'Ridge', 'SimpleImputer'): R² = 0.9881
('NoneType', 'Lasso', 'SimpleImputer'): R² = 0.9670
('NoneType', 'ElasticNet', 'SimpleImputer'): R² = 0.9267
('NoneType', 'KNeighborsRegressor', 'SimpleImputer'): R² = 0.6059
('LocalOutlierFactor', 'LinearRegression', 'SimpleImputer'): R² = 0.9730
('LocalOutlierFactor', 'Ridge', 'SimpleImputer'): R² = 0.9866
('LocalOutlierFactor', 'Lasso', 'SimpleImputer'): R² = 0.9611
('LocalOutlierFactor', 'ElasticNet', 'SimpleImputer'): R² = 0.9200
('LocalOutlierFactor', 'KNeighborsRegressor', 'SimpleImputer'): R² = 0.5542
('IsolationForest', 'LinearRegression', 'SimpleImputer'): R² = 0.9720
('IsolationForest', 'Ridge', 'SimpleImputer'): R² = 0.9863
('IsolationForest', 'Lasso', 'SimpleImputer'): R² = 0.9627
('IsolationForest', 'ElasticNet', 'SimpleImputer'): R² = 0.9189
('IsolationForest', 'KNeighborsRegressor', 'SimpleImputer'): R² = 0.5427


## [06] Model Testing

In [42]:
################################################################################
# 모형 평가
################################################################################

for model_name, model in models.items():
    print(f"Evaluating model: {model_name}")

    y_test_pred = model.predict(X_test)
    y_test_pred = pd.DataFrame(
        y_test_pred, 
        columns=[col + "_PREDICTED" for col in y_test.columns], 
        index=y_test.index
    )

    # 테스트 세트 성능 측정
    r2_test = model.score(X_test, y_test)
    print(f"Test R²  : {r2_test:.4f}")

Evaluating model: ('NoneType', 'LinearRegression', 'SimpleImputer')
Test R²  : -1.0072
Evaluating model: ('NoneType', 'Ridge', 'SimpleImputer')
Test R²  : -1.0563
Evaluating model: ('NoneType', 'Lasso', 'SimpleImputer')
Test R²  : -1.0457
Evaluating model: ('NoneType', 'ElasticNet', 'SimpleImputer')
Test R²  : -0.9580
Evaluating model: ('NoneType', 'KNeighborsRegressor', 'SimpleImputer')
Test R²  : -0.7042
Evaluating model: ('LocalOutlierFactor', 'LinearRegression', 'SimpleImputer')
Test R²  : -0.9663
Evaluating model: ('LocalOutlierFactor', 'Ridge', 'SimpleImputer')
Test R²  : -1.0622
Evaluating model: ('LocalOutlierFactor', 'Lasso', 'SimpleImputer')
Test R²  : -1.0455
Evaluating model: ('LocalOutlierFactor', 'ElasticNet', 'SimpleImputer')
Test R²  : -0.9557
Evaluating model: ('LocalOutlierFactor', 'KNeighborsRegressor', 'SimpleImputer')
Test R²  : -0.7216
Evaluating model: ('IsolationForest', 'LinearRegression', 'SimpleImputer')
Test R²  : -9.4823
Evaluating model: ('IsolationForest'

## [07] Ensemble Models

## [08]  Best Auto Outlier Remover Selection

In [45]:
import numpy as np

# Auto Outlier Remover와 관련된 모든 모델의 성능 출력
average_scores = {}
best_remover = None
highest_average_score = float('-inf')

# auto_outlier_removers 리스트를 사용하여, 개별 remover의 평균 성능 계산 --> 가장 높은 평균성능을 보인 remover 선택
for remover in auto_outlier_removers:
    remover_name = remover.__class__.__name__

    # 해당 Outlier Remover에 속한 모델 필터링
    related_models = {
        model_key: score for model_key, score in performances.items()
        if model_key[0] == remover_name
    }

    # 평균 R² 계산 (관련된 모델이 있을 경우만 처리)
    if related_models:
        average_score = np.mean(list(related_models.values()))  # 평균 R² 계산
        average_scores[remover_name] = average_score  # 평균 성능 저장

        # 최고 평균 성능 업데이트
        if average_score > highest_average_score:
            highest_average_score = average_score
            best_remover = remover

# 선택된 auto_outlier_remover와 관련된 모델 출력
print(f"Best Auto Outlier Remover (Highest Average R²): {best_remover.__class__.__name__}")
print(f"Average R²: {highest_average_score:.4f}\n")

print(f"All Models with the Best Auto Outlier Remover ({best_remover.__class__.__name__}):")
best_models = [] 
for model_key, score in performances.items():
    if model_key[0] == best_remover.__class__.__name__:
        best_models.append((model_key, models[key]))  
        print(f"Model: {model_key}, R²: {score:.4f}")

Best Auto Outlier Remover (Highest Average R²): NoneType
Average R²: 0.8936

All Models with the Best Auto Outlier Remover (NoneType):
Model: ('NoneType', 'LinearRegression', 'SimpleImputer'), R²: 0.9801
Model: ('NoneType', 'Ridge', 'SimpleImputer'), R²: 0.9881
Model: ('NoneType', 'Lasso', 'SimpleImputer'), R²: 0.9670
Model: ('NoneType', 'ElasticNet', 'SimpleImputer'), R²: 0.9267
Model: ('NoneType', 'KNeighborsRegressor', 'SimpleImputer'), R²: 0.6059


## [09]  VotingClassifier

In [46]:
################################################################################
# 전처리
################################################################################
from sklearn.ensemble import VotingRegressor
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV
import numpy as np
from itertools import product

# 훈련된 모델들을 이용해 VotingClassifier 앙상블 구성
ensemble = VotingRegressor(estimators=best_models)

# 가중치 조정을 위한 하이퍼파라미터 설정 (각 리스트에는 algorithms에 포함된 알고리즘 수만큼의 가중치가 필요)
# 예시:
# params = {
#     'weights': [
#         [1, 0, 0],
#         [0, 1, 0],
#         [0, 0, 1],
#         [0.5, 0.2, 0.3],
#         [0.5, 0.3, 0.2],
#         # 필요한 만큼 다양한 가중치 조합을 추가 가능 (합계가 1이 되어야 하는 것은 아니며, 상대적 비율로 계산됨)
#     ]
# }
# 가중치 값으로 0, 1, 2 중 하나를 부여 --> 예: [0, 0, 1], [2, 1, 0] 위에는 다섯 개가 되어야 함. 꼭 합이 1이 아니어도 됨 상대적임
# 1. 가중치 조합 생성
weights = []

# 모든 조합 생성: [0, 1] 범위 내에서 best_models의 길이만큼 반복
for combination in product(range(0, 2), repeat=len(best_models)):
    # 모든 원소가 0인 조합은 제외
    if any(combination):
        weights.append(list(combination))

# 2. GridSearchCV에 사용할 파라미터 딕셔너리 구성
params = {'weights': weights}

# 생성된 가중치 조합 출력
print("Generated weights:", weights)

# 3. GridSearchCV 객체 생성 및 설정
search = GridSearchCV(
    estimator=ensemble,       # 앙상블 모델 (사전에 정의된 모델)
    param_grid=params,        # 가중치 조합을 검색할 파라미터
    cv=5,                     # 5-폴드 교차검증
    scoring='r2',             # R² 점수를 평가 지표로 사용
    n_jobs=-1                 # 병렬 처리로 속도 향상
)
# 4. 출력 메시지 정리
print("GridSearchCV initialized with weight combinations.")

################################################################################
# 앙상블 모형 훈련
################################################################################
################################################################################
# 데이터 전처리 및 최적화된 앙상블 모델 학습
################################################################################

# 1. 결측치 처리
# 1.1 특정 열에 결측치 포함된 행 제거
X_train = X_train.dropna(subset=[drop_na_features])
y_train = y_train.loc[X_train.index]

# 2. 이상치 제거
# 2.1 도메인 지식 활용 이상치 제거
X_train, y_train = remove_domain_outliers(X_train, y_train)

# 2.2 자동 이상치 제거기 적용
if best_remover is not None:
    # 결측값 대체
    imputer = SimpleImputer(strategy='median')
    X_train_imputed = imputer.fit_transform(X_train[numeric_features])
    
    # 자동 이상치 제거기로 inlier 마스크 생성
    y_train_inlier = best_remover.fit_predict(X_train_imputed)
    inlier_mask_train = y_train_inlier != -1  # inlier만 True
else:
    # best_remover가 None인 경우, 모든 데이터를 inlier로 간주
    inlier_mask_train = np.ones(X_train.shape[0], dtype=bool)

# inlier 마스크를 기반으로 데이터 필터링
X_train, y_train = X_train[inlier_mask_train], y_train[inlier_mask_train]

# 3. GridSearchCV로 가중치 조정 및 최적 앙상블 모델 훈련
search.fit(X_train, y_train.values.ravel())

# 4. 최적화된 모델 출력
best_ensemble = search.best_estimator_
print(f"Best Ensemble Weights: {search.best_params_}")
print(f"Best Cross-validated R²: {search.best_score_:.4f}")

################################################################################
# 최적화된 앙상블 모델 성능 평가
################################################################################

# 훈련 세트 성능 평가
ensemble_train_score = best_ensemble.score(X_train, y_train)
print(f"Ensemble Model Training R²: {ensemble_train_score:.4f} (Potential risk of overfitting)")

# 테스트 세트 성능 평가
ensemble_test_score = best_ensemble.score(X_test, y_test)
print(f"Ensemble Model Test R²: {ensemble_test_score:.4f}")



Generated weights: [[0, 0, 0, 0, 1], [0, 0, 0, 1, 0], [0, 0, 0, 1, 1], [0, 0, 1, 0, 0], [0, 0, 1, 0, 1], [0, 0, 1, 1, 0], [0, 0, 1, 1, 1], [0, 1, 0, 0, 0], [0, 1, 0, 0, 1], [0, 1, 0, 1, 0], [0, 1, 0, 1, 1], [0, 1, 1, 0, 0], [0, 1, 1, 0, 1], [0, 1, 1, 1, 0], [0, 1, 1, 1, 1], [1, 0, 0, 0, 0], [1, 0, 0, 0, 1], [1, 0, 0, 1, 0], [1, 0, 0, 1, 1], [1, 0, 1, 0, 0], [1, 0, 1, 0, 1], [1, 0, 1, 1, 0], [1, 0, 1, 1, 1], [1, 1, 0, 0, 0], [1, 1, 0, 0, 1], [1, 1, 0, 1, 0], [1, 1, 0, 1, 1], [1, 1, 1, 0, 0], [1, 1, 1, 0, 1], [1, 1, 1, 1, 0], [1, 1, 1, 1, 1]]
GridSearchCV initialized with weight combinations.


/Users/jinyong/anaconda3/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:227: UserWarning: Found unknown categories in columns [0, 2, 5] during transform. These unknown categories will be encoded as all zeros
  warnings.warn(
/Users/jinyong/anaconda3/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:227: UserWarning: Found unknown categories in columns [2, 5] during transform. These unknown categories will be encoded as all zeros
  warnings.warn(
/Users/jinyong/anaconda3/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:227: UserWarning: Found unknown categories in columns [2, 5] during transform. These unknown categories will be encoded as all zeros
  warnings.warn(
/Users/jinyong/anaconda3/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:227: UserWarning: Found unknown categories in columns [0, 2, 5] during transform. These unknown categories will be encoded as all zeros
  warnings.warn(
/Users/jinyong/anaconda3/lib/python3.1

Best Ensemble Weights: {'weights': [0, 0, 0, 0, 1]}
Best Cross-validated R²: 0.5427
Ensemble Model Training R²: 1.0000 (Potential risk of overfitting)
Ensemble Model Test R²: -0.6540
